In [43]:
def get_linguistic_data(url_input):
    import urllib3
    from bs4 import BeautifulSoup
    import re
    import numpy as np

    http = urllib3.PoolManager()
    url = url_input
    response = http.request("GET", url)
    html_doc = response.data
    soup = BeautifulSoup(html_doc,features="html.parser")

    match_phrases = ["distribution","classification","proto","subdivisions","ethnicity",
                     "early","speakers","native","family","population","writing","extinct",
                     "region","dialects","era","standard","revival","reconstruction",
                    "reconstructed","reconstructions"]
    
    match_phrases_1 = ["reconstruction","reconstructed","reconstructions"]
    
    for i in soup.body.find_all("tbody"):
        try:
            if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                table = i
                break
        except:
            pass
    dictionary = {}
    delimiter = '###' 
    
    for line_break in table.findAll('br'):  
        line_break.replaceWith(delimiter)
    dictionary["English Name"] = re.sub("\[([a-zA-Z]| |\d)+\]|^vte|vte?","",(" ".join(table.tr.th.get_text().split(delimiter))))
    dictionary["URL"] = url_input
    
    i = 0
    for j in table.find_all("th"):
        if re.compile("writing",re.I).search(j.get_text()) != None:
            i += 1
    if i >= 1:
        dictionary["Name in Local Language"] = []
    else:
        dictionary["Other Names"] = []
        
    for tag in table.find_all("tr")[1:3]:
        if tag.find_all("th") == [] and tag.find_all("td") != []:
            if tag.find_all(["li","i","span"]) == []:
                i = 0
                for j in table.find_all("th"):
                    if re.compile("writing",re.I).search(j.get_text()) != None:
                        i += 1
                if i >= 1:
                    text_3 = " ".join(tag.get_text().split(delimiter))
                    text_4 = re.sub("\\u200e","",text_3)
                    if text_4 not in dictionary["Name in Local Language"] and text_4 != "" and len(text_4) <= 40:
                        dictionary["Name in Local Language"].append(text_4)
                else:
                    text_3 = " ".join(tag.get_text().split(delimiter))
                    text_4 = re.sub("\\u200e","",text_3)
                    if text_4 not in dictionary["Other Names"] and text_4 != "" and len(text_4) <= 40:
                        dictionary["Other Names"].append(text_4)
            else:
                i = 0
                for j in table.find_all("th"):
                    if re.compile("writing",re.I).search(j.get_text()) != None:
                        i += 1
                if i >= 1:
                    for n in tag.find_all(["li","i","span"]):
                        list_4 = []
                        m = n.find_next_sibling()
                        if m != None:
                            while m.name != "i":
                                if m.name != "i" and m.name != "span":
                                    text_1 = "".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,m.get_text()))
                                    text_1 = " ".join(re.split(re.compile(r"\[([a-zA-Z]| |\d)+\]"), text_1)).strip(" ")
                                    if text_1 not in list_4 and text_1 != "" and len(text_1) <= 40:
                                        list_4.append(text_1)
                                else:
                                    break
                                if m.find_next_sibling() != None:
                                    m = m.find_next_sibling()
                                else:
                                    break
                        text = " ".join(n.get_text().split(delimiter))+" "+" ".join(list_4)
                        text = " ".join(re.split(re.compile(r"\[([a-zA-Z]| |\d)+\]"), text)).strip()
                        text = re.sub("\\n|\\u200e","",text)
                        if text not in dictionary["Name in Local Language"] and text != "" and len(text) <= 40:
                            dictionary["Name in Local Language"].append(text)
                else:
                    for n in tag.find_all(["li","i","span"]):
                        list_4 = []
                        m = n.find_next_sibling()
                        if m != None:
                            while m.name != "i" and m.name != "span":
                                if m.name != "i" and m.name != "span":
                                    text_1 = "".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,m.find_next_sibling().get_text()))
                                    text_1 = " ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), text_1)).strip()
                                    if text_1 not in list_4 and text_1 != "" and len(text_1) <= 40:
                                        list_4.append(text_1)
                                else:
                                    break
                                if m.find_next_sibling() != None:
                                    m = m.find_next_sibling()
                                else:
                                    break
                        text = " ".join(n.get_text().split(delimiter))+" "+" ".join(list_4)
                        text = " ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), text)).strip()
                        text = re.sub("\\n|\\u200e","",text)
                        if text not in dictionary["Other Names"] and text != "" and len(text) <= 40:
                            dictionary["Other Names"].append(text)

    for phrase_1 in match_phrases_1:
        if re.compile(r""+phrase_1,re.I).search(table.get_text()) != None:
            dictionary["Status"] = "Reconstructed Language"
        else:
            dictionary["Status"] = "Normal"
            
    for tag in table.find_all("th"):
        for phrase in match_phrases:
            if re.compile(r""+phrase,re.I).search(tag.get_text()) != None:
                if tag.parent.td != None:
                    if tag.parent.td.find_all("li") == []:
                        if re.compile(r"native",re.I).search(tag.get_text()) == None:
                            key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                            value = [x for x in re.split('\\n|c.\\u2009|\\xa0|'+delimiter, tag.parent.td.get_text()) if x != ""]
                            key = " ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), key))
                            value = [" ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), i)).strip(" ") for i in value]
                            if value not in list(dictionary.values()) and value not in list(dictionary.keys()) and value != "" and key not in list(dictionary.values()) and key not in list(dictionary.keys()) and key != "":
                                dictionary[key] = value      
                        else:
                            key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                            value = [x for x in re.split('\\n|c.\\u2009|\\xa0|'+delimiter, tag.parent.td.get_text()) if x != ""]
                            key = " ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), key))
                            value = " ".join([" ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), i)).strip(" ") for i in value]).strip(" | ")
                            if value not in list(dictionary.values()) and value not in list(dictionary.keys()) and value != "" and key not in list(dictionary.values()) and key not in list(dictionary.keys()) and key != "":
                                dictionary[key] = value
                    elif tag.parent.td.find("li").find_next_sibling("li") != None:
                        list_1 = []
                        key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                        for i in tag.parent.td.find_all("li"):
                            value = [x for x in re.split('\\n|c.\\u2009|\\xa0|'+delimiter, i.get_text()) if x != ""]
                            value = [" ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), i)).strip(" ") for i in value]
                            value = [" ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), i)).strip(" ") for i in value]
                            value = " ".join(value)
                            try: 
                                if re.compile(re.escape("†|+"),re.I).search(i.get_text()) != None:
                                    value += " †"
                            except:
                                pass
                            try: 
                                if re.compile(re.escape("?"),re.I).search(i.get_text()) != None:
                                    value = "(?) "+value
                            except:
                                pass
                            if "?" in value:
                                value = re.sub("\(\?\) \(\?\)", "(?)",value)
                                value = value.rstrip("(?)").strip(" ")
                            list_1.append(value)
                            list_1 = sorted(list_1, key=len)
                            list_3 = []
                            for i in list_1:
                                b = 0
                                for j in list_3:
                                    if j in i:
                                        b += 1
                                if b == 0:
                                    list_3.append(i)
                        value_2 = [re.sub("\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?","",i) for i in list_3]
                        value = value_2
                        if value not in list(dictionary.values()) and value not in list(dictionary.keys()) and value != "" and key not in list(dictionary.values()) and key not in list(dictionary.keys()) and key != "":
                            dictionary[key] = value
                    else:
                        list_1 = []
                        key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                        for i in tag.parent.td.find_all(["li","a","b"]):
                            value = [x for x in re.split('\\n|c.\\u2009|\\xa0|'+delimiter, i.find(text=True)) if x != ""]
                            value = [" ".join(re.split(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]"), i)).strip(" ") for i in value]
                            value = " ".join(value)
                            try: 
                                if re.compile(re.escape("†|+"),re.I).search(i.parent.find(text=True)) != None:
                                    value += " †"
                            except:
                                pass
                            try: 
                                if re.compile(re.escape("?"),re.I).search(i.parent.find(text=True)) != None:
                                    value = "(?) "+value
                            except:
                                pass
                            value = re.sub("\(\?\) \(\?\)", "(?)",value)
                            value = re.sub("citation needed", " ",value)
                            value = re.sub("\\n|\[([a-zA-Z]| |\d)+\]", "",value)
                            list_1.append(value)
                        value_1 = [i for i in list_1 if i != "" and re.match(r'^.*[a-zA-Z]+.*$', i) != None]
                        value_2 = [re.sub("^vte|vte?","",i) for i in value_1]
                        value = []
                        for i in value_2:
                            if i not in value:
                                value.append(i)
                        if value not in list(dictionary.values()) and value not in list(dictionary.keys()) and value != "" and key not in list(dictionary.values()) and key not in list(dictionary.keys()) and key != "":
                            dictionary[key] = value
                            
    for tag in table.find_all("td"):
        try:
            if tag.div.find_all("div") != []:
                if len(tag.div.find_all("div")) > 1:
                    if tag.div.find_all("p") == []:
                        list_1 = []
                        for i in tag.div.find_all("div"):
                            text = "".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,i.get_text()))
                            if len(text) <= 45:
                                list_1.append(text)
                        if np.mean(list(map(lambda x: len(x),list_1))) < 35:
                            dictionary["Sub Languages"] = list_1
                    else:
                        dict_1 = {}
                        for i in tag.div.find_all("p"):
                            list_2 = []
                            j = i.find_next_sibling()
                            while j.name != "p":
                                if j.name == "div":
                                    list_2.append("".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,j.get_text())))
                                if j.find_next_sibling() != None:
                                    j = j.find_next_sibling()
                                else:
                                    break
                            list_2 = [x for x in list_2 if x != ""]
                            if np.mean(list(map(lambda x: len(x),list_2))) < 35:
                                dict_1["".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,i.get_text()))] = list_2
                                dictionary["Sub Languages"] = dict_1  
        except:
            pass
    list_4 = ["Language family","Early form","Linguistic classification","Dialect","Subdivision","Proto"]
    url_list = []
    for tag in table.find_all("th"):
        for phrase in list_4:
            if re.compile(r""+phrase,re.I).search(tag.get_text()) != None:
                if tag.parent.td != None:
                    if tag.parent.td.find_all("li") == []:
                        key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                        list_3 = []
                        list_3.append(re.sub("\[([a-zA-Z]| |\d)+\]|^vte|vte?|\\n|c.\\u2009|\\xa0|","",tag.parent.td.get_text()))
                        dictionary[key+" corrected"]=list_3
                    else:
                        key = " ".join(re.split('\\n|c.\\u2009|\\xa0|'+delimiter,tag.get_text()))
                        list_3 = []
                        if tag.parent.td.find_all("a",recursive=False) != []:
                            url_1 = "https://en.wikipedia.org"+tag.parent.td.find("a",recursive=False).get("href")
                            list_3.append(\
                                          re.sub("\[([a-zA-Z]| |\d)+\]|^vte|vte?|\\n|c.\\u2009|\\xa0|","",tag.parent.td.find("a",recursive=False).find(text=True, recursive=False)))
                            url_list.append(url_1)
                        if tag.parent.td.find_all("div",recursive=False) != []:
                            i = tag.parent.td.find("div",recursive=False)
                            if i.find_all("a",recursive=False) == []:
                                if i.find_all(["b","span","i"],recursive=False)==[]:
                                    value = i.find(text=True)
                                    value = re.sub('\\n|c.\\u2009|\\xa0|'+delimiter,"", value)
                                    value = re.sub('\(.*\)',"", value)
                                    value = re.sub(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?"),"", value).strip(" ")
                                    list_3.append(value)
                                else:
                                    if i.find(["b","span","i"],recursive=False).find_all("a") == []:
                                        value = i.find(["b","span","i"],recursive=False).find(text=True)
                                        value = re.sub('\\n|c.\\u2009|\\xa0|'+delimiter,"", value)
                                        value = re.sub('\(.*\)',"", value)
                                        value = re.sub(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?"),"", value).strip(" ")
                                        list_3.append(value)
                                    else:
                                        if "not exist" in i.find(["b","span","i"],recursive=False).find("a").get('title'):
                                            list_3.append(i.find(["b","span","i"],recursive=False).find("a").get_text())
                                        else:
                                            url_1 = "https://en.wikipedia.org"+i.find(["b","span","i"],recursive=False).find("a").get('href')
                                            response_1 = http.request("GET", url_1)
                                            html_doc_1 = response_1.data
                                            soup_1 = BeautifulSoup(html_doc_1,features="html.parser")
                                            for i in soup_1.body.find_all("tbody"):
                                                try:
                                                    if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                                                        table_1 = i
                                                        name_1 = re.sub("\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?","",(" ".join(table_1.tr.th.get_text().split(delimiter))))
                                                        url_list.append(url_1)
                                                        list_3.append(name_1)
                                                        break
                                                except:
                                                    pass        
                            else:
                                if "not exist" in i.find("a",recursive=False).get('title'):
                                    list_3.append(i.find("a",recursive=False).get_text())
                                else:
                                    url_1 = "https://en.wikipedia.org"+i.find("a",recursive=False).get('href')
                                    response_1 = http.request("GET", url_1)
                                    html_doc_1 = response_1.data
                                    soup_1 = BeautifulSoup(html_doc_1,features="html.parser")
                                    for i in soup_1.body.find_all("tbody"):
                                        try:
                                            if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                                                table_1 = i
                                                name_1 = " ".join(table_1.tr.th.get_text().split(delimiter))
                                                name_1 = re.sub("\\n|^vte|vte?","",name_1)
                                                url_list.append(url_1)
                                                list_3.append(name_1)
                                                break
                                        except:
                                            pass
                        for i in tag.parent.td.find_all("li"):
                            if i.find_all("a",recursive=False)==[]:
                                if i.find_all(["b","span","i"],recursive=False)==[]:
                                    value = i.find(text=True, recursive=False)
                                    value = re.sub('\\n|c.\\u2009|\\xa0|'+delimiter,"", value)
                                    value = re.sub('\(.*\)',"", value)
                                    value = re.sub(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?"),"", value).strip(" ")
                                    list_3.append(value)
                                else:
                                    if i.find(["b","span","i"],recursive=False).find_all("a") == []:
                                        value = i.find(["b","span","i"],recursive=False).find(text=True)
                                        value = re.sub('\\n|c.\\u2009|\\xa0|'+delimiter,"", value)
                                        value = re.sub('\(.*\)',"", value)
                                        value = re.sub(re.compile(r"\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?"),"", value).strip(" ")
                                        list_3.append(value)
                                    else:
                                        if "not exist" in i.find(["b","span","i"],recursive=False).find("a").get('title'):
                                            list_3.append(i.find(["b","span","i"],recursive=False).find("a").get_text())
                                        else:
                                            url_1 = "https://en.wikipedia.org"+i.find(["b","span","i"],recursive=False).find("a",recursive=False).get('href')
                                            response_1 = http.request("GET", url_1)
                                            html_doc_1 = response_1.data
                                            soup_1 = BeautifulSoup(html_doc_1,features="html.parser")
                                            for i in soup_1.body.find_all("tbody"):
                                                try:
                                                    if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                                                        table_1 = i
                                                        name_1 = re.sub("\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?","",(" ".join(table_1.tr.th.get_text().split(delimiter))))
                                                        url_list.append(url_1)
                                                        list_3.append(name_1)
                                                        break
                                                except:
                                                    pass               
                            else:
                                if "not exist" in i.find("a",recursive=False).get('title'):
                                    list_3.append(i.find("a",recursive=False).get_text())
                                else:
                                    url_1 = "https://en.wikipedia.org"+i.find("a",recursive=False).get('href')
                                    response_1 = http.request("GET", url_1)
                                    html_doc_1 = response_1.data
                                    soup_1 = BeautifulSoup(html_doc_1,features="html.parser")
                                    for i in soup_1.body.find_all("tbody"):
                                        try:
                                            if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                                                table_1 = i
                                                name_1 = re.sub("\\n|\[([a-zA-Z]| |\d)+\]|^vte|vte?","",(" ".join(table_1.tr.th.get_text().split(delimiter))))
                                                url_list.append(url_1)
                                                list_3.append(name_1)
                                                break
                                        except:
                                            pass                      
                        dictionary[key+" corrected"]=list_3
    dictionary["Related URLs"]=url_list

    dictionary = {dictionary["English Name"]:dictionary}
    return dictionary

In [35]:
def get_related_url(url_input):
    import urllib3
    from bs4 import BeautifulSoup
    import re

    http = urllib3.PoolManager()
    url = url_input
    response = http.request("GET", url)
    html_doc = response.data
    soup = BeautifulSoup(html_doc,features="html.parser")

    match_phrases = ["classification","proto","subdivisions",
                     "early","family","dialects","standard","reconstruction",
                    "reconstructed","reconstructions"]
    match_phrases_1 = ["classification","subdivisions","subgrouping","dialects",
                      "subclassification","languages","ancest","branch"]
                     
    for i in soup.body.find_all("tbody"):
        try:
            if i.tr.th["colspan"] == "2":
                table = i
                break
        except:
            pass
        
    delimiter = '###' 
    for line_break in table.findAll('br'):  
        line_break.replaceWith(delimiter)

    url_list = []
    for tag in table.find_all("th"):
        for phrase in match_phrases:
            if re.compile(r""+phrase,re.I).search(tag.get_text()) != None:
                if tag.parent.td != None:
                    if tag.parent.td.find_all("li") == []:# no list in tag
                        if re.compile(r"native",re.I).search(tag.get_text()) == None:
                            if tag.parent.td.find_all("a") != []:
                                for i in tag.parent.td.find_all("a"):
                                    url_list.append(i.get('href'))
                        else:
                            if tag.parent.td.find_all("a") != []:
                                for i in tag.parent.td.find_all("a"):
                                    url_list.append(i.get('href'))
                    elif tag.parent.td.find("li").find_next_sibling("li") != None: # paralleled lists in a division
                        for i in tag.parent.td.find_all("li"):
                            if i.find_all("a") != []:
                                for j in i.find_all("a"):
                                    url_list.append(j.get('href'))
                    else: # nested list within list
                        for i in tag.parent.td.find_all(["li","a","b"]):
                            if i.name == "a":
                                url_list.append(i.get('href'))
                            elif i.find_all("a") != []:
                                for j in i.find_all("a"):
                                    url_list.append(j.get('href'))
    for tag in table.find_all("td"):
        try:
            if tag.div.find_all("div") != []:
                if len(tag.div.find_all("div")) > 1:
                    for i in tag.div.find_all("div"):
                        if tag.find_all("a") != []:
                            for j in i.find_all("a"):
                                url_list.append(j.get('href'))
        except:
            pass
        
    for i in soup.body.find_all("tbody"):
        try:
            if i.tr.th["colspan"] == "2":
                table = i
                break
        except:
            pass
    if soup.find_all("h2") != []:
        for n in soup.find_all("h2"):
            i = 0
            for phrase in match_phrases_1:
                if re.compile(r""+phrase,re.I).search(n.get_text()) != None:
                    i += 1
            if i >= 1:
                tag = n.find_next_sibling()
                while tag.name != "h2":
                    if tag.find_all("a") != []:
                        for k in tag.find_all("a"):
                            url_list.append(k.get('href'))
                    if tag.find_next_sibling() != None:
                        tag = tag.find_next_sibling()
                    else:
                        break
            
    unwanted_list = ['/wiki/First_language','/wiki/Second_language','/wiki/Language_family']
    url_list_2 = []
    for i in url_list:
        if i != None:
            if i not in url_list_2 and i not in unwanted_list and i.startswith("/wiki/"):
                url_list_2.append(i)
    url_list = ["https://en.wikipedia.org"+i for i in url_list_2]
    return url_list

In [36]:
def Merge(dict1, dict2):
    res = {**dict1, **dict2}
    return res

In [37]:
def check_language_family(language_family_list,url_input):
    import urllib3
    from bs4 import BeautifulSoup
    import re

    http = urllib3.PoolManager()
    url = url_input
    response = http.request("GET", url)
    html_doc = response.data
    soup = BeautifulSoup(html_doc,features="html.parser")
    
    for i in soup.body.find_all("tbody"):
        try:
            if i.tr.th["colspan"] == "2" and "infobox" in i.parent.get("class"):
                table = i
                break
        except:
            pass
    a = 0
    text = table.get_text()
    text_2 = ", ".join([i.get_text() for i in table.find_all("th")])
    if language_family_list == ["Altaic"]:
        language_family_list = ["Altaic","Turkic","Mongolic","Tungusic","Koreanic","Japonic","Ainu"]
        for i in language_family_list:
            if re.compile(r""+i,re.I).search(text) != None:
                a += 1
        if a >= 1 and re.compile("language|linguistic|reconstruct",re.I).search(text_2) != None:
            return True
        else:
            return False
    elif language_family_list == ["Afroasiatic"]:
        language_family_list = ["Afroasiatic","Afro-Asiatic","Asiatic","Afro-"]
        for i in language_family_list:
            if re.compile(r""+i,re.I).search(text) != None:
                a += 1
        if a >= 1 and re.compile("language|linguistic|reconstruct",re.I).search(text_2) != None:
            return True
        else:
            return False
    else:
        for i in language_family_list:
            if re.compile(r""+i,re.I).search(text) != None:
                a += 1
        if a >= 1 and re.compile("language|linguistic|reconstruct",re.I).search(text_2) != None:
            return True
        else:
            return False

In [51]:
def get_language_family_data(language_family,number,additional_start_url_list=[]):
    import time
    from collections import deque

    start_url = "https://en.wikipedia.org/wiki/"+language_family+"_languages"
    unsearched_url_list = [start_url]+additional_start_url_list
    searched_url_list = []
    found_url_list = []
    languages_dict = {}
    deque = deque(unsearched_url_list)
    
    while len(found_url_list) <= number and len(deque) > 0:
        if len(deque) <= 5:
            for i in unsearched_url_list[unsearched_url_list.index(deque[-1])+1:]:
                deque.append(i)
        url = deque.popleft()
        try:
            language_family_list = [language_family]
            if check_language_family(language_family_list,url):
                new_language_dict = get_linguistic_data(url)
                for key in new_language_dict.keys():
                    if key not in languages_dict.keys():
                        languages_dict = Merge(languages_dict,new_language_dict)
                        print("Now scraping from     "+url)
                        print("New linguistic unit is     "+key)
                        found_url_list.append(url)
                        searched_url_list.append(url)
                        try:
                            print("      found_url_list index: "+str(found_url_list.index(url)))
                            print("      searched_url_list index: "+str(searched_url_list.index(url)))
                            print("      unsearched_url_list index: "+str(unsearched_url_list.index(url)))
                        except:
                            pass
                    else:
                        print("         Have already looked at this one   "+url)
                        try:
                            print("               found_url_list index: "+str(found_url_list.index(url)))
                        except:
                            pass
                        try:
                            print("               searched_url_list index: "+str(searched_url_list.index(url)))
                        except:
                            pass
                        try:
                            print("               unsearched_url_list index: "+str(unsearched_url_list.index(url)))
                        except:
                            pass
                for url_1 in get_related_url(url):
                    new_url = url_1
                    if new_url not in unsearched_url_list and new_url not in searched_url_list:
                        deque.append(new_url)
                    if new_url not in unsearched_url_list:
                        unsearched_url_list.append(new_url)
                print("                       deque length: "+str(len(deque)))
                print("                       found_url_list length: "+str(len(found_url_list)))
                print("                       searched_url_list length: "+str(len(searched_url_list)))
                print("                       unsearched_url_list length: "+str(len(unsearched_url_list)))
                print("                       "+str(len(languages_dict.keys()))+" languages in the dictionary")
                time.sleep(0)
            else:
                print("                  This one does not belong here   "+url)
                searched_url_list.append(url)
                try:
                    print("                         searched_url_list index: "+str(searched_url_list.index(url)))
                    print("                         unsearched_url_list index: "+str(unsearched_url_list.index(url)))
                except:
                    pass
        except:
            pass
    return languages_dict

In [6]:
def write_to_json(data,file_name):
    import json
    data_json = json.dumps(data)
    with open(file_name, "w") as outfile:
        outfile.write(data_json)

In [7]:
def read_from_json(file_name):
    import json
    with open(file_name, "r",encoding="UTF-8") as outfile:
        read_data = outfile.read()
    return json.loads(read_data)

In [8]:
language_family_list = ["Indo-European","Sino-Tibetan","Austronesian","Uralic"
                   "Niger–Congo","Dravidian","Austroasiatic","Afroasiatic","Altaic"]

In [9]:
test_language_family_list = ["Indo-European","Sino-Tibetan","Altaic","Uralic","Afroasiatic"]

In [54]:
name = "Indo-European"
additional_start_url_list = get_related_url("https://en.wikipedia.org/wiki/List_of_Indo-European_languages")
write_to_json(get_language_family_data(name,5000,additional_start_url_list),name+" language data.json")

Now scraping from     https://en.wikipedia.org/wiki/Indo-European_languages
New linguistic unit is     Indo-European
      found_url_list index: 0
      searched_url_list index: 0
      unsearched_url_list index: 0
                       deque length: 4077
                       found_url_list length: 1
                       searched_url_list length: 1
                       unsearched_url_list length: 4078
                       1 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/List_of_Afro-Asiatic_languages
                         searched_url_list index: 1
                         unsearched_url_list index: 2
                  This one does not belong here   https://en.wikipedia.org/wiki/List_of_Tungusic_languages
                         searched_url_list index: 2
                         unsearched_url_list index: 5
Now scraping from     https://en.wikipedia.org/wiki/Proto-Indo-European_language
New linguistic unit is  

         Have already looked at this one   https://en.wikipedia.org/wiki/Indo-European_languages
               found_url_list index: 0
               searched_url_list index: 0
               unsearched_url_list index: 0
                       deque length: 4477
                       found_url_list length: 14
                       searched_url_list length: 19
                       unsearched_url_list length: 4511
                       14 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Pontic%E2%80%93Caspian_steppe
                         searched_url_list index: 19
                         unsearched_url_list index: 37
                  This one does not belong here   https://en.wikipedia.org/wiki/Danube
                         searched_url_list index: 20
                         unsearched_url_list index: 41
Now scraping from     https://en.wikipedia.org/wiki/Proto-Italic_language
New linguistic unit is     Proto-Itali

         Have already looked at this one   https://en.wikipedia.org/wiki/Pre-Proto-Indo-European
               unsearched_url_list index: 77
                       deque length: 4779
                       found_url_list length: 25
                       searched_url_list length: 37
                       unsearched_url_list length: 4857
                       25 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Anatolian
New linguistic unit is     Proto-Anatolian
      found_url_list index: 25
      searched_url_list index: 37
      unsearched_url_list index: 78
                       deque length: 4778
                       found_url_list length: 26
                       searched_url_list length: 38
                       unsearched_url_list length: 4857
                       26 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Luwian_language
New linguistic unit is     Luwian
      found_url_list index: 26
      s

Now scraping from     https://en.wikipedia.org/wiki/Western_Iranian_languages
New linguistic unit is     Western Iranian
      found_url_list index: 37
      searched_url_list index: 49
      unsearched_url_list index: 96
                       deque length: 4850
                       found_url_list length: 38
                       searched_url_list length: 50
                       unsearched_url_list length: 4947
                       38 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Nuristani
New linguistic unit is     Nuristani
      found_url_list index: 38
      searched_url_list index: 50
      unsearched_url_list index: 97
                       deque length: 4852
                       found_url_list length: 39
                       searched_url_list length: 51
                       unsearched_url_list length: 4950
                       39 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Indo-Ary

Now scraping from     https://en.wikipedia.org/wiki/Elbe_Germanic
New linguistic unit is     Elbe Germanic
      found_url_list index: 53
      searched_url_list index: 65
      unsearched_url_list index: 116
                       deque length: 5031
                       found_url_list length: 54
                       searched_url_list length: 66
                       unsearched_url_list length: 5148
                       54 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Weser-Rhine_Germanic
New linguistic unit is     Weser-Rhine Germanic
      found_url_list index: 54
      searched_url_list index: 66
      unsearched_url_list index: 117
                       deque length: 5031
                       found_url_list length: 55
                       searched_url_list length: 67
                       unsearched_url_list length: 5149
                       55 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/North_Sea_

...

                       deque length: 201
                       found_url_list length: 1186
                       searched_url_list length: 5733
                       unsearched_url_list length: 10221
                       1186 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Leeuwarden
                         searched_url_list index: 5733
                         unsearched_url_list index: 10020
                  This one does not belong here   https://en.wikipedia.org/wiki/Vatra_Dornei
                         searched_url_list index: 5734
                         unsearched_url_list index: 10021
                  This one does not belong here   https://en.wikipedia.org/wiki/C%C3%A2mpulung_Moldovenesc
                         searched_url_list index: 5735
                         unsearched_url_list index: 10022
                  This one does not belong here   https://en.wikipedia.org/wiki/Moldova_(river)
               

                  This one does not belong here   https://en.wikipedia.org/wiki/Mon_language
                         searched_url_list index: 5753
                         unsearched_url_list index: 10056
                  This one does not belong here   https://en.wikipedia.org/wiki/Taiwanese_Hokkien
                         searched_url_list index: 5754
                         unsearched_url_list index: 10057
                  This one does not belong here   https://en.wikipedia.org/wiki/Mon-Khmer_languages
                         searched_url_list index: 5755
                         unsearched_url_list index: 10058
                  This one does not belong here   https://en.wikipedia.org/wiki/Cambodian_language
                         searched_url_list index: 5756
                         unsearched_url_list index: 10059
                  This one does not belong here   https://en.wikipedia.org/wiki/Ilocano_language
                         searched_url_list index: 5757
      

                  This one does not belong here   https://en.wikipedia.org/wiki/Old_Order_Mennonites
                         searched_url_list index: 5787
                         unsearched_url_list index: 10108
                  This one does not belong here   https://en.wikipedia.org/wiki/Elkhart_County
                         searched_url_list index: 5788
                         unsearched_url_list index: 10109
                  This one does not belong here   https://en.wikipedia.org/wiki/LaGrange_County
                         searched_url_list index: 5789
                         unsearched_url_list index: 10110
                  This one does not belong here   https://en.wikipedia.org/wiki/Parke_County
                         searched_url_list index: 5790
                         unsearched_url_list index: 10111
                  This one does not belong here   https://en.wikipedia.org/wiki/New_Ulm,_Minnesota
                         searched_url_list index: 5791
         

                  This one does not belong here   https://en.wikipedia.org/wiki/Krrab%C3%AB
                         searched_url_list index: 5818
                         unsearched_url_list index: 10148
                  This one does not belong here   https://en.wikipedia.org/wiki/Peqin
                         searched_url_list index: 5819
                         unsearched_url_list index: 10149
                  This one does not belong here   https://en.wikipedia.org/wiki/Librazhd
                         searched_url_list index: 5820
                         unsearched_url_list index: 10150
                  This one does not belong here   https://en.wikipedia.org/wiki/Quk%C3%ABs
                         searched_url_list index: 5821
                         unsearched_url_list index: 10152
                  This one does not belong here   https://en.wikipedia.org/wiki/Prrenjas
                         searched_url_list index: 5822
                         unsearched_url_list i

                  This one does not belong here   https://en.wikipedia.org/wiki/Municipalities_and_cities_of_Serbia
                         searched_url_list index: 5858
                         unsearched_url_list index: 10194
                  This one does not belong here   https://en.wikipedia.org/wiki/Dushmani_(tribe)
                         searched_url_list index: 5859
                         unsearched_url_list index: 10206
         Have already looked at this one   https://en.wikipedia.org/wiki/Tosk_language
               unsearched_url_list index: 10208
                       deque length: 24
                       found_url_list length: 1188
                       searched_url_list length: 5860
                       unsearched_url_list length: 10233
                       1188 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Abruzzi
                         searched_url_list index: 5860
                         

In [55]:
name = "Sino-Tibetan"
additional_start_url_list = []
write_to_json(get_language_family_data(name,5000,additional_start_url_list),name+" language data.json")

Now scraping from     https://en.wikipedia.org/wiki/Sino-Tibetan_languages
New linguistic unit is     Sino-Tibetan
      found_url_list index: 0
      searched_url_list index: 0
      unsearched_url_list index: 0
                       deque length: 116
                       found_url_list length: 1
                       searched_url_list length: 1
                       unsearched_url_list length: 117
                       1 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Sino-Tibetan_language
New linguistic unit is     Proto-Sino-Tibetan
      found_url_list index: 1
      searched_url_list index: 1
      unsearched_url_list index: 1
                       deque length: 116
                       found_url_list length: 2
                       searched_url_list length: 2
                       unsearched_url_list length: 118
                       2 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Sinitic_languag

         Have already looked at this one   https://en.wikipedia.org/wiki/Karen_languages
               unsearched_url_list index: 28
                       deque length: 611
                       found_url_list length: 14
                       searched_url_list length: 23
                       unsearched_url_list length: 640
                       14 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Tibeto-Burman_languages
               unsearched_url_list index: 29
                       deque length: 610
                       found_url_list length: 14
                       searched_url_list length: 23
                       unsearched_url_list length: 640
                       14 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Henri_Maspero
                         searched_url_list index: 23
                         unsearched_url_list index: 31
                  Th

Now scraping from     https://en.wikipedia.org/wiki/Bodish_languages
New linguistic unit is     Bodish
      found_url_list index: 28
      searched_url_list index: 40
      unsearched_url_list index: 52
                       deque length: 728
                       found_url_list length: 29
                       searched_url_list length: 41
                       unsearched_url_list length: 781
                       29 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Lepcha_language
New linguistic unit is     Lepcha
      found_url_list index: 29
      searched_url_list index: 41
      unsearched_url_list index: 53
                       deque length: 731
                       found_url_list length: 30
                       searched_url_list length: 42
                       unsearched_url_list length: 785
                       30 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Dhimal_languages
New linguistic unit is

Now scraping from     https://en.wikipedia.org/wiki/Tshangla_language
New linguistic unit is     Tshangla
      found_url_list index: 44
      searched_url_list index: 57
      unsearched_url_list index: 71
                       deque length: 855
                       found_url_list length: 45
                       searched_url_list length: 58
                       unsearched_url_list length: 927
                       45 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Newaric_languages
New linguistic unit is     Newaric
      found_url_list index: 45
      searched_url_list index: 58
      unsearched_url_list index: 72
                       deque length: 854
                       found_url_list length: 46
                       searched_url_list length: 59
                       unsearched_url_list length: 927
                       46 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Raji%E2%80%93Raute_languages
New 

         Have already looked at this one   https://en.wikipedia.org/wiki/Macro-Bai_languages
               unsearched_url_list index: 90
                       deque length: 870
                       found_url_list length: 59
                       searched_url_list length: 73
                       unsearched_url_list length: 961
                       59 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Northern_Qiang_language
New linguistic unit is     Northern Qiang
      found_url_list index: 59
      searched_url_list index: 73
      unsearched_url_list index: 91
                       deque length: 871
                       found_url_list length: 60
                       searched_url_list length: 74
                       unsearched_url_list length: 963
                       60 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Southern_Qiang_language
New linguistic unit is     Southern Qiang
      found_url_list in

...

         Have already looked at this one   https://en.wikipedia.org/wiki/Topolect
               unsearched_url_list index: 2348
                       deque length: 122
                       found_url_list length: 726
                       searched_url_list length: 1673
                       unsearched_url_list length: 2471
                       726 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Xide_County
                         searched_url_list index: 1673
                         unsearched_url_list index: 2349
                  This one does not belong here   https://en.wikipedia.org/wiki/Xundian_County
                         searched_url_list index: 1674
                         unsearched_url_list index: 2350
                  This one does not belong here   https://en.wikipedia.org/wiki/Shilin_County
                         searched_url_list index: 1675
                         unsearched_url_list index: 235

                  This one does not belong here   https://en.wikipedia.org/wiki/Pu%27an_County
                         searched_url_list index: 1712
                         unsearched_url_list index: 2390
                  This one does not belong here   https://en.wikipedia.org/wiki/Qinglong_County,_Guizhou
                         searched_url_list index: 1713
                         unsearched_url_list index: 2391
                  This one does not belong here   https://en.wikipedia.org/wiki/Fuyuan_County,_Yunnan
                         searched_url_list index: 1714
                         unsearched_url_list index: 2392
                  This one does not belong here   https://en.wikipedia.org/wiki/Luoping_County
                         searched_url_list index: 1715
                         unsearched_url_list index: 2393
                  This one does not belong here   https://en.wikipedia.org/wiki/Xundian_Hui_and_Yi_Autonomous_County
                         searched_url_

                       deque length: 53
                       found_url_list length: 729
                       searched_url_list length: 1732
                       unsearched_url_list length: 2473
                       729 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Northern_Muji_language
               unsearched_url_list index: 2420
                       deque length: 52
                       found_url_list length: 729
                       searched_url_list length: 1732
                       unsearched_url_list length: 2473
                       729 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Qila_Muji_language
               unsearched_url_list index: 2421
                       deque length: 51
                       found_url_list length: 729
                       searched_url_list length: 1732
                       unsearched_url_list length: 2473
        

         Have already looked at this one   https://en.wikipedia.org/wiki/Alugu_language
               unsearched_url_list index: 2439
                       deque length: 33
                       found_url_list length: 736
                       searched_url_list length: 1739
                       unsearched_url_list length: 2473
                       736 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Xiqi_language
New linguistic unit is     Xiqi
      found_url_list index: 736
      searched_url_list index: 1739
      unsearched_url_list index: 2440
                       deque length: 32
                       found_url_list length: 737
                       searched_url_list length: 1740
                       unsearched_url_list length: 2473
                       737 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Ati_language_(China)
New linguistic unit is     Ati
      found_url_list index: 737
      searched_

         Have already looked at this one   https://en.wikipedia.org/wiki/Syuba_language
               unsearched_url_list index: 2467
                       deque length: 9
                       found_url_list length: 743
                       searched_url_list length: 1761
                       unsearched_url_list length: 2477
                       743 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Tichurong_language
New linguistic unit is     Tichurong
      found_url_list index: 743
      searched_url_list index: 1761
      unsearched_url_list index: 2468
                       deque length: 8
                       found_url_list length: 744
                       searched_url_list length: 1762
                       unsearched_url_list length: 2477
                       744 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Walungge_language
               unsearched_url_list index: 2469
     

In [52]:
name = "Uralic"
additional_start_url_list = []
write_to_json(get_language_family_data(name,5000,additional_start_url_list),name+" language data.json")

Now scraping from     https://en.wikipedia.org/wiki/Uralic_languages
New linguistic unit is     Uralic
      found_url_list index: 0
      searched_url_list index: 0
      unsearched_url_list index: 0
                       deque length: 39
                       found_url_list length: 1
                       searched_url_list length: 1
                       unsearched_url_list length: 40
                       1 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Uralic_language
New linguistic unit is     Proto-Uralic
      found_url_list index: 1
      searched_url_list index: 1
      unsearched_url_list index: 1
                       deque length: 40
                       found_url_list length: 2
                       searched_url_list length: 2
                       unsearched_url_list length: 42
                       2 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Finnic_languages
New linguistic unit is    

                       deque length: 246
                       found_url_list length: 18
                       searched_url_list length: 18
                       unsearched_url_list length: 265
                       18 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Sami_languages
               unsearched_url_list index: 19
                       deque length: 245
                       found_url_list length: 18
                       searched_url_list length: 18
                       unsearched_url_list length: 265
                       18 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Merya_language
New linguistic unit is     Meryan
      found_url_list index: 18
      searched_url_list index: 18
      unsearched_url_list index: 20
                       deque length: 247
                       found_url_list length: 19
                       searched_url_list length: 19
                     

Now scraping from     https://en.wikipedia.org/wiki/Leivu_dialect
New linguistic unit is     Leivu
      found_url_list index: 32
      searched_url_list index: 35
      unsearched_url_list index: 52
                       deque length: 231
                       found_url_list length: 33
                       searched_url_list length: 36
                       unsearched_url_list length: 284
                       33 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Ludza_dialect
New linguistic unit is     Ludza
      found_url_list index: 33
      searched_url_list index: 36
      unsearched_url_list index: 53
                       deque length: 230
                       found_url_list length: 34
                       searched_url_list length: 37
                       unsearched_url_list length: 284
                       34 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Seto_language
New linguistic unit is     Seto


         Have already looked at this one   https://en.wikipedia.org/wiki/Samoyed_languages
               unsearched_url_list index: 83
                       deque length: 222
                       found_url_list length: 43
                       searched_url_list length: 56
                       unsearched_url_list length: 306
                       43 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Meadow_Mari
New linguistic unit is     Meadow Mari
      found_url_list index: 43
      searched_url_list index: 56
      unsearched_url_list index: 88
                       deque length: 217
                       found_url_list length: 44
                       searched_url_list length: 57
                       unsearched_url_list length: 306
                       44 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Hill_Mari
New linguistic unit is     Hill Mari
      found_url_list index: 44
      searched_url_list inde

                       deque length: 222
                       found_url_list length: 55
                       searched_url_list length: 73
                       unsearched_url_list length: 335
                       55 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Northern_Sami_language
               unsearched_url_list index: 113
                       deque length: 221
                       found_url_list length: 55
                       searched_url_list length: 73
                       unsearched_url_list length: 335
                       55 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Kemi_S%C3%A1mi_language
New linguistic unit is     Kemi Sámi
      found_url_list index: 55
      searched_url_list index: 73
      unsearched_url_list index: 116
                       deque length: 218
                       found_url_list length: 56
                       searched_url_list length: 74

                       deque length: 194
                       found_url_list length: 64
                       searched_url_list length: 87
                       unsearched_url_list length: 337
                       64 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Forest_Nenets_language
New linguistic unit is     Forest Nenets
      found_url_list index: 64
      searched_url_list index: 87
      unsearched_url_list index: 143
                       deque length: 193
                       found_url_list length: 65
                       searched_url_list length: 88
                       unsearched_url_list length: 337
                       65 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Selkup_language
New linguistic unit is     Selkup
      found_url_list index: 65
      searched_url_list index: 88
      unsearched_url_list index: 144
                       deque length: 192
                       found_url_li

                  This one does not belong here   https://en.wikipedia.org/wiki/Maltese_language
                         searched_url_list index: 115
                         unsearched_url_list index: 201
                  This one does not belong here   https://en.wikipedia.org/wiki/European_Union
                         searched_url_list index: 116
                         unsearched_url_list index: 202
                  This one does not belong here   https://en.wikipedia.org/wiki/Indo-European_language
                         searched_url_list index: 117
                         unsearched_url_list index: 203
                  This one does not belong here   https://en.wikipedia.org/wiki/Tallinn
                         searched_url_list index: 118
                         unsearched_url_list index: 208
                  This one does not belong here   https://en.wikipedia.org/wiki/Tartu
                         searched_url_list index: 119
                         unsearched_u

                  This one does not belong here   https://en.wikipedia.org/wiki/Balsfjord
                         searched_url_list index: 150
                         unsearched_url_list index: 259
                  This one does not belong here   https://en.wikipedia.org/wiki/Jukkasj%C3%A4rvi
                         searched_url_list index: 151
                         unsearched_url_list index: 260
                  This one does not belong here   https://en.wikipedia.org/wiki/Ofotfjord
                         searched_url_list index: 152
                         unsearched_url_list index: 261
                  This one does not belong here   https://en.wikipedia.org/wiki/Tana_(Norway)
                         searched_url_list index: 153
                         unsearched_url_list index: 263
                  This one does not belong here   https://en.wikipedia.org/wiki/Tana_bru
                         searched_url_list index: 154
                         unsearched_url_list i

         Have already looked at this one   https://en.wikipedia.org/wiki/Hill_Mari_language
               unsearched_url_list index: 306
                       deque length: 36
                       found_url_list length: 72
                       searched_url_list length: 177
                       unsearched_url_list length: 343
                       72 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Kosa_River
                         searched_url_list index: 177
                         unsearched_url_list index: 308
                  This one does not belong here   https://en.wikipedia.org/wiki/Kochyovsky_District
                         searched_url_list index: 178
                         unsearched_url_list index: 309
                  This one does not belong here   https://en.wikipedia.org/wiki/Afanasyevsky_District
                         searched_url_list index: 179
                         unsearched_url_list

Now scraping from     https://en.wikipedia.org/wiki/Yukaghir_languages
New linguistic unit is     Yukaghir
      found_url_list index: 74
      searched_url_list index: 198
      unsearched_url_list index: 342
                       deque length: 20
                       found_url_list length: 75
                       searched_url_list length: 199
                       unsearched_url_list length: 363
                       75 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Uralic%E2%80%93Yukaghir_languages
New linguistic unit is     Uralic–Yukaghir
      found_url_list index: 75
      searched_url_list index: 199
      unsearched_url_list index: 343
                       deque length: 19
                       found_url_list length: 76
                       searched_url_list length: 200
                       unsearched_url_list length: 363
                       76 languages in the dictionary
                  This one does not belong here   https:

In [53]:
name = "Altaic"
additional_start_url_list = []
write_to_json(get_language_family_data(name,5000,additional_start_url_list),name+" language data.json")

Now scraping from     https://en.wikipedia.org/wiki/Altaic_languages
New linguistic unit is     Altaic
      found_url_list index: 0
      searched_url_list index: 0
      unsearched_url_list index: 0
                       deque length: 7
                       found_url_list length: 1
                       searched_url_list length: 1
                       unsearched_url_list length: 8
                       1 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Altaic_language
New linguistic unit is     Proto-Altaic
      found_url_list index: 1
      searched_url_list index: 1
      unsearched_url_list index: 1
                       deque length: 11
                       found_url_list length: 2
                       searched_url_list length: 2
                       unsearched_url_list length: 13
                       2 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Turkic_languages
New linguistic unit is     T

Now scraping from     https://en.wikipedia.org/wiki/Moghol_language
New linguistic unit is     Mogholi
      found_url_list index: 15
      searched_url_list index: 15
      unsearched_url_list index: 19
                       deque length: 261
                       found_url_list length: 16
                       searched_url_list length: 16
                       unsearched_url_list length: 281
                       16 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Para-Mongolic_languages
New linguistic unit is     Para-Mongolic
      found_url_list index: 16
      searched_url_list index: 16
      unsearched_url_list index: 21
                       deque length: 267
                       found_url_list length: 17
                       searched_url_list length: 17
                       unsearched_url_list length: 289
                       17 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Khitan_language
New ling

Now scraping from     https://en.wikipedia.org/wiki/Ruanruan_language
New linguistic unit is     Ruan-ruan
      found_url_list index: 32
      searched_url_list index: 33
      unsearched_url_list index: 44
                       deque length: 314
                       found_url_list length: 33
                       searched_url_list length: 34
                       unsearched_url_list length: 359
                       33 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Rouran_Khaganate
New linguistic unit is     Rouran Khaganate
      found_url_list index: 33
      searched_url_list index: 34
      unsearched_url_list index: 45
                       deque length: 313
                       found_url_list length: 34
                       searched_url_list length: 35
                       unsearched_url_list length: 359
                       34 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/w

                  This one does not belong here   https://en.wikipedia.org/wiki/Songhua_River
                         searched_url_list index: 54
                         unsearched_url_list index: 71
                  This one does not belong here   https://en.wikipedia.org/wiki/Jin_Dynasty_(1115-1234)
                         searched_url_list index: 55
                         unsearched_url_list index: 72
                  This one does not belong here   https://en.wikipedia.org/wiki/Qing_Dynasty
                         searched_url_list index: 56
                         unsearched_url_list index: 73
                  This one does not belong here   https://en.wikipedia.org/wiki/Manchu_dynasty
                         searched_url_list index: 57
                         unsearched_url_list index: 74
                  This one does not belong here   https://en.wikipedia.org/wiki/China
                         searched_url_list index: 58
                         unsearched_url_lis

Now scraping from     https://en.wikipedia.org/wiki/Baekje_language
New linguistic unit is     Baekje
      found_url_list index: 53
      searched_url_list index: 78
      unsearched_url_list index: 102
                       deque length: 374
                       found_url_list length: 54
                       searched_url_list length: 79
                       unsearched_url_list length: 477
                       54 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Korean_dialects
               unsearched_url_list index: 104
                       deque length: 372
                       found_url_list length: 54
                       searched_url_list length: 79
                       unsearched_url_list length: 477
                       54 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Yanbian_Korean_Autonomous_Prefecture
                         searched_url_list

...

                  This one does not belong here   https://en.wikipedia.org/wiki/East_Azerbaijan_Province
                         searched_url_list index: 576
                         unsearched_url_list index: 850
                  This one does not belong here   https://en.wikipedia.org/wiki/West_Azerbaijan_Province
                         searched_url_list index: 577
                         unsearched_url_list index: 851
                  This one does not belong here   https://en.wikipedia.org/wiki/Ardabil_Province
                         searched_url_list index: 578
                         unsearched_url_list index: 852
                  This one does not belong here   https://en.wikipedia.org/wiki/Zanjan_Province
                         searched_url_list index: 579
                         unsearched_url_list index: 853
                  This one does not belong here   https://en.wikipedia.org/wiki/Tehran
                         searched_url_list index: 580
                

                  This one does not belong here   https://en.wikipedia.org/wiki/Voiceless_glottal_fricative
                         searched_url_list index: 604
                         unsearched_url_list index: 898
                  This one does not belong here   https://en.wikipedia.org/wiki/Voiceless_postalveolar_affricate
                         searched_url_list index: 605
                         unsearched_url_list index: 901
                  This one does not belong here   https://en.wikipedia.org/wiki/Voiceless_alveolo-palatal_fricative
                         searched_url_list index: 606
                         unsearched_url_list index: 902
                  This one does not belong here   https://en.wikipedia.org/wiki/Voiced_alveolo-palatal_fricative
                         searched_url_list index: 607
                         unsearched_url_list index: 904
                  This one does not belong here   https://en.wikipedia.org/wiki/Voiced_palatal_approximant
   

                  This one does not belong here   https://en.wikipedia.org/wiki/Vagaysky_District
                         searched_url_list index: 633
                         unsearched_url_list index: 947
                  This one does not belong here   https://en.wikipedia.org/wiki/Yarkovsky_District
                         searched_url_list index: 634
                         unsearched_url_list index: 948
                  This one does not belong here   https://en.wikipedia.org/wiki/Tevrizsky_District
                         searched_url_list index: 635
                         unsearched_url_list index: 949
                  This one does not belong here   https://en.wikipedia.org/wiki/Ust-Ishimsky_District
                         searched_url_list index: 636
                         unsearched_url_list index: 950
                  This one does not belong here   https://en.wikipedia.org/wiki/Znamensky_District,_Omsk_Oblast
                         searched_url_list index: 

                  This one does not belong here   https://en.wikipedia.org/wiki/Ruoqiang_Town
                         searched_url_list index: 661
                         unsearched_url_list index: 985
         Have already looked at this one   https://en.wikipedia.org/wiki/Orkhon_Turkic
               unsearched_url_list index: 989
                       deque length: 63
                       found_url_list length: 211
                       searched_url_list length: 662
                       unsearched_url_list length: 1053
                       211 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Old_Uyghur
               unsearched_url_list index: 990
                       deque length: 62
                       found_url_list length: 211
                       searched_url_list length: 662
                       unsearched_url_list length: 1053
                       211 languages in the dictionary
         Have already loo

                       deque length: 22
                       found_url_list length: 211
                       searched_url_list length: 682
                       unsearched_url_list length: 1053
                       211 languages in the dictionary
         Have already looked at this one   https://en.wikipedia.org/wiki/Altaic_language#Controversy
               unsearched_url_list index: 1031
                       deque length: 21
                       found_url_list length: 211
                       searched_url_list length: 682
                       unsearched_url_list length: 1053
                       211 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Tal%C3%A2t_Tekin
                         searched_url_list index: 682
                         unsearched_url_list index: 1032
                  This one does not belong here   https://en.wikipedia.org/wiki/Altai_Republic
                         searched_url_lis

In [56]:
name = "Afroasiatic"
additional_start_url_list = []
write_to_json(get_language_family_data(name,5000,additional_start_url_list),name+" language data.json")

Now scraping from     https://en.wikipedia.org/wiki/Afroasiatic_languages
New linguistic unit is     Afroasiatic
      found_url_list index: 0
      searched_url_list index: 0
      unsearched_url_list index: 0
                       deque length: 69
                       found_url_list length: 1
                       searched_url_list length: 1
                       unsearched_url_list length: 70
                       1 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Proto-Afroasiatic_language
New linguistic unit is     Proto-Afroasiatic
      found_url_list index: 1
      searched_url_list index: 1
      unsearched_url_list index: 1
                       deque length: 72
                       found_url_list length: 2
                       searched_url_list length: 2
                       unsearched_url_list length: 74
                       2 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Berber_languages
New li

                  This one does not belong here   https://en.wikipedia.org/wiki/Nama_language
                         searched_url_list index: 23
                         unsearched_url_list index: 34
                  This one does not belong here   https://en.wikipedia.org/wiki/Carl_Meinhof
                         searched_url_list index: 24
                         unsearched_url_list index: 36
                  This one does not belong here   https://en.wikipedia.org/wiki/Fula_language
                         searched_url_list index: 25
                         unsearched_url_list index: 37
                  This one does not belong here   https://en.wikipedia.org/wiki/Maasai_language
                         searched_url_list index: 26
                         unsearched_url_list index: 38
                  This one does not belong here   https://en.wikipedia.org/wiki/Bari_language
                         searched_url_list index: 27
                         unsearched_url_list

Now scraping from     https://en.wikipedia.org/wiki/Northern_Berber_languages
New linguistic unit is     Northern Berber
      found_url_list index: 19
      searched_url_list index: 49
      unsearched_url_list index: 75
                       deque length: 180
                       found_url_list length: 20
                       searched_url_list length: 50
                       unsearched_url_list length: 256
                       20 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Western_Berber_languages
New linguistic unit is     Western Berber
      found_url_list index: 20
      searched_url_list index: 50
      unsearched_url_list index: 76
                       deque length: 179
                       found_url_list length: 21
                       searched_url_list length: 51
                       unsearched_url_list length: 256
                       21 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Tuar

Now scraping from     https://en.wikipedia.org/wiki/Zenaga_language
New linguistic unit is     Zenaga
      found_url_list index: 37
      searched_url_list index: 67
      unsearched_url_list index: 93
                       deque length: 245
                       found_url_list length: 38
                       searched_url_list length: 68
                       unsearched_url_list length: 339
                       38 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Atlas_languages
New linguistic unit is     Atlas languages
      found_url_list index: 38
      searched_url_list index: 68
      unsearched_url_list index: 95
                       deque length: 244
                       found_url_list length: 39
                       searched_url_list length: 69
                       unsearched_url_list length: 340
                       39 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Zenati_languages
New linguistic

Now scraping from     https://en.wikipedia.org/wiki/Masa_languages
New linguistic unit is     Masa
      found_url_list index: 49
      searched_url_list index: 92
      unsearched_url_list index: 127
                       deque length: 407
                       found_url_list length: 50
                       searched_url_list length: 93
                       unsearched_url_list length: 535
                       50 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/West_Chadic_languages
New linguistic unit is     West Chadic
      found_url_list index: 50
      searched_url_list index: 93
      unsearched_url_list index: 128
                       deque length: 497
                       found_url_list length: 51
                       searched_url_list length: 94
                       unsearched_url_list length: 626
                       51 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Agaw_languages
New linguistic 

...

         Have already looked at this one   https://en.wikipedia.org/wiki/Damascus_Arabic
               unsearched_url_list index: 1345
                       deque length: 229
                       found_url_list length: 508
                       searched_url_list length: 826
                       unsearched_url_list length: 1575
                       508 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Said_Akl
                         searched_url_list index: 826
                         unsearched_url_list index: 1346
         Have already looked at this one   https://en.wikipedia.org/wiki/Semitic_language
               unsearched_url_list index: 1347
                       deque length: 227
                       found_url_list length: 508
                       searched_url_list length: 827
                       unsearched_url_list length: 1575
                       508 languages in the dictionary
                 

                  This one does not belong here   https://en.wikipedia.org/wiki/Meknes
                         searched_url_list index: 858
                         unsearched_url_list index: 1399
                  This one does not belong here   https://en.wikipedia.org/wiki/Marrakesh
                         searched_url_list index: 859
                         unsearched_url_list index: 1400
                  This one does not belong here   https://en.wikipedia.org/wiki/Jebala_people
                         searched_url_list index: 860
                         unsearched_url_list index: 1401
                  This one does not belong here   https://en.wikipedia.org/wiki/Ghomaras
                         searched_url_list index: 861
                         unsearched_url_list index: 1403
                  This one does not belong here   https://en.wikipedia.org/wiki/Zenata
                         searched_url_list index: 862
                         unsearched_url_list index: 140

                       deque length: 118
                       found_url_list length: 511
                       searched_url_list length: 895
                       unsearched_url_list length: 1576
                       511 languages in the dictionary
                  This one does not belong here   https://en.wikipedia.org/wiki/Persian_language
                         searched_url_list index: 895
                         unsearched_url_list index: 1458
                  This one does not belong here   https://en.wikipedia.org/wiki/Urdu
                         searched_url_list index: 896
                         unsearched_url_list index: 1459
Now scraping from     https://en.wikipedia.org/wiki/Emirati_Arabic
New linguistic unit is     Emirati Arabic
      found_url_list index: 511
      searched_url_list index: 897
      unsearched_url_list index: 1460
                       deque length: 115
                       found_url_list length: 512
                       searched_url_

                  This one does not belong here   https://en.wikipedia.org/wiki/Lake_Urmia
                         searched_url_list index: 925
                         unsearched_url_list index: 1517
                  This one does not belong here   https://en.wikipedia.org/wiki/Sopurghan
                         searched_url_list index: 926
                         unsearched_url_list index: 1519
                  This one does not belong here   https://en.wikipedia.org/wiki/Naghadeh
                         searched_url_list index: 927
                         unsearched_url_list index: 1520
                  This one does not belong here   https://en.wikipedia.org/wiki/Salmas
                         searched_url_list index: 928
                         unsearched_url_list index: 1521
                  This one does not belong here   https://en.wikipedia.org/wiki/Sanandaj
                         searched_url_list index: 929
                         unsearched_url_list index: 1522

         Have already looked at this one   https://en.wikipedia.org/wiki/Hassaniyya
               unsearched_url_list index: 1575
                       deque length: 1
                       found_url_list length: 516
                       searched_url_list length: 959
                       unsearched_url_list length: 1577
                       516 languages in the dictionary
Now scraping from     https://en.wikipedia.org/wiki/Neo-Mandaic
New linguistic unit is     Neo-Mandaic
      found_url_list index: 516
      searched_url_list index: 959
      unsearched_url_list index: 1576
                       deque length: 0
                       found_url_list length: 517
                       searched_url_list length: 960
                       unsearched_url_list length: 1577
                       517 languages in the dictionary
